# Word Embeddings

In [11]:
import pandas as pd
import numpy as np
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.preprocessing import MinMaxScaler
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import f1_score
from sklearn.model_selection import GridSearchCV
from sklearn.naive_bayes import ComplementNB
from sklearn.svm import LinearSVC
from sklearn.ensemble import RandomForestClassifier
from sklearn.dummy import DummyClassifier
import gensim.downloader as api
from gensim.models import KeyedVectors
import gensim

In [2]:
test_df = pd.read_csv("../../data/prepared/test.csv")
train_df = pd.read_csv("../../data/prepared/train.csv")
valid_df = pd.read_csv("../../data/prepared/valid.csv")
unlabeled_df = pd.read_csv("../../data/prepared/unlabeled.csv")
bigger_train_df = pd.concat([train_df, valid_df], ignore_index=True)
results = {}

## Most Common and Stratified Baselines

In [3]:
baseline_classifier = DummyClassifier(strategy='most_frequent', random_state=42)
baseline_classifier.fit(train_df["problem_abstract"], train_df["team"])
y_pred = baseline_classifier.predict(test_df["problem_abstract"])
results["dummy most common"] = f1_score(test_df["team"], y_pred, average='micro')
print("F1-micro Score on Test Set:", results["dummy most common"])

baseline_classifier = DummyClassifier(strategy='stratified', random_state=42)
baseline_classifier.fit(train_df["problem_abstract"], train_df["team"])
y_pred = baseline_classifier.predict(test_df["problem_abstract"])
results["dummy stratified"] = f1_score(test_df["team"], y_pred, average='micro')
print("F1-micro Score on Test Set:", results["dummy stratified"])

F1-micro Score on Test Set: 0.3333333333333333
F1-micro Score on Test Set: 0.18984547461368653


## Log Regression

In [4]:


# Function to convert text into averaged word embeddings
def text_to_avg_vector(text, model):
    words = text.split()
    words_in_vocab = [word for word in words if word in model.key_to_index]
    if len(words_in_vocab) == 0:
        return np.zeros(model.vector_size)
    avg_vector = np.mean([model[word] for word in words_in_vocab], axis=0)
    return avg_vector

def transform_with_embeddings(df, model):
    return np.array(df['problem_abstract'].apply(lambda s: text_to_avg_vector("" if s is None or pd.isna(s) else s, model)).tolist())

word2vec_model = KeyedVectors.load_word2vec_format('../../models/GoogleNews-vectors-negative300.bin', binary=True)
glove_model = KeyedVectors.load_word2vec_format('../../models/glove.840B.300d.txt', binary=False, no_header=True)
# Transform train and test data
X_train_word2vec = transform_with_embeddings(train_df, word2vec_model)
X_train_glove = transform_with_embeddings(train_df, glove_model)
y_train = train_df['team']
X_test_word2vec = transform_with_embeddings(test_df, word2vec_model)
X_test_glove = transform_with_embeddings(test_df, glove_model)
y_test = test_df['team']

In [5]:
def finetune(X_train, y_train, model, param_grid, metric, cv=5, verbose=2):

    grid_search = GridSearchCV(model, param_grid, cv=5, scoring=metric, verbose=verbose)
    grid_search.fit(X_train, y_train)
    best_model = grid_search.best_estimator_
    best_params = grid_search.best_params_
    return best_model, best_params

def evaluate(X_test, y_test, model):

    y_pred = model.predict(X_test)
    metric = f1_score(y_test, y_pred, average="micro")
    return metric

In [6]:
model, model_params = finetune(
    X_train_word2vec, 
    y_train,
    LogisticRegression(random_state=42, penalty="elasticnet", class_weight="balanced", n_jobs=-1, solver="saga"),
    {
        "C": [0.01, 0.1, 1.0, 10.0],
        "l1_ratio": [0.0, 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9, 1.0]
    },
    "f1_micro",
    cv=5,
    verbose=2
    )
print("Best Hyperparameters:", model_params)
results["logistic regression word2vec"] = evaluate(X_test_word2vec, y_test, model)
print("F1-micro Score on Test Set:", results["logistic regression word2vec"])

Fitting 5 folds for each of 44 candidates, totalling 220 fits


/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/model_selection/_split.py:725: UserWarning: The least populated class in y has only 1 members, which is less than n_splits=5.
  warnings.warn(


[CV] END ...............................C=0.01, l1_ratio=0.0; total time=   5.5s
[CV] END ...............................C=0.01, l1_ratio=0.0; total time=   6.6s
[CV] END ...............................C=0.01, l1_ratio=0.0; total time=   4.8s
[CV] END ...............................C=0.01, l1_ratio=0.0; total time=   6.3s
[CV] END ...............................C=0.01, l1_ratio=0.0; total time=  11.0s
[CV] END ...............................C=0.01, l1_ratio=0.1; total time=   6.1s
[CV] END ...............................C=0.01, l1_ratio=0.1; total time=   4.8s
[CV] END ...............................C=0.01, l1_ratio=0.1; total time=   6.4s
[CV] END ...............................C=0.01, l1_ratio=0.1; total time=   9.1s
[CV] END ...............................C=0.01, l1_ratio=0.1; total time=   9.1s
[CV] END ...............................C=0.01, l1_ratio=0.2; total time=   2.7s
[CV] END ...............................C=0.01, l1_ratio=0.2; total time=   4.8s
[CV] END ...................

/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:350: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(


[CV] END ................................C=0.1, l1_ratio=0.0; total time=  30.0s


...

/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:350: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(


[CV] END ...............................C=10.0, l1_ratio=1.0; total time=  48.1s


/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:350: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(


[CV] END ...............................C=10.0, l1_ratio=1.0; total time=  46.7s
Best Hyperparameters: {'C': 10.0, 'l1_ratio': 0.5}
F1-micro Score on Test Set: 0.5342163355408388


/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:350: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(


In [7]:
model, model_params = finetune(
    X_train_glove, 
    y_train,
    LogisticRegression(random_state=42, penalty="elasticnet", class_weight="balanced", n_jobs=-1, solver="saga"),
    {
        "C": [0.01, 0.1, 1.0, 10.0],
        "l1_ratio": [0.0, 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9, 1.0]
    },
    "f1_micro",
    cv=5,
    verbose=2
    )
print("Best Hyperparameters:", model_params)
results["logistic regression glove"] = evaluate(X_test_glove, y_test, model)
print("F1-micro Score on Test Set:", results["logistic regression glove"])

/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/model_selection/_split.py:725: UserWarning: The least populated class in y has only 1 members, which is less than n_splits=5.
  warnings.warn(


Fitting 5 folds for each of 44 candidates, totalling 220 fits


/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:350: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(


[CV] END ...............................C=0.01, l1_ratio=0.0; total time=  17.1s


/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:350: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(


...

/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:350: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(


[CV] END ...............................C=10.0, l1_ratio=1.0; total time=  40.1s


/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:350: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(


[CV] END ...............................C=10.0, l1_ratio=1.0; total time=  38.6s
Best Hyperparameters: {'C': 10.0, 'l1_ratio': 0.0}
F1-micro Score on Test Set: 0.565121412803532


/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/linear_model/_sag.py:350: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(


## Naive Bayes

In [13]:
scaler_word2vec = MinMaxScaler()
scaler_word2vec.fit(X_train_word2vec)
model, model_params = finetune(
    X_train_word2vec, 
    y_train,
    ComplementNB(),
    {
        "norm": [True, False],
        "alpha": [0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9, 1.0],
        
    },
    "f1_micro",
    cv=5,
    verbose=2,
    )
print("Best Hyperparameters:", model_params)
results["naive bayes word2vec"] = evaluate(X_test_word2vec, y_test, model)
print("F1-micro Score on Test Set:", results["naive bayes word2vec"])

Fitting 5 folds for each of 20 candidates, totalling 100 fits
[CV] END ...............................alpha=0.1, norm=True; total time=   0.0s
[CV] END ...............................alpha=0.1, norm=True; total time=   0.0s
[CV] END ...............................alpha=0.1, norm=True; total time=   0.0s
[CV] END ...............................alpha=0.1, norm=True; total time=   0.0s
[CV] END ...............................alpha=0.1, norm=True; total time=   0.0s
[CV] END ..............................alpha=0.1, norm=False; total time=   0.0s
[CV] END ..............................alpha=0.1, norm=False; total time=   0.0s
[CV] END ..............................alpha=0.1, norm=False; total time=   0.0s
[CV] END ..............................alpha=0.1, norm=False; total time=   0.0s
[CV] END ..............................alpha=0.1, norm=False; total time=   0.0s
[CV] END ...............................alpha=0.2, norm=True; total time=   0.0s
[CV] END ...............................alpha=0

/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/model_selection/_split.py:725: UserWarning: The least populated class in y has only 1 members, which is less than n_splits=5.
  warnings.warn(


[CV] END ..............................alpha=0.3, norm=False; total time=   0.0s
[CV] END ...............................alpha=0.4, norm=True; total time=   0.0s
[CV] END ...............................alpha=0.4, norm=True; total time=   0.0s
[CV] END ...............................alpha=0.4, norm=True; total time=   0.0s
[CV] END ...............................alpha=0.4, norm=True; total time=   0.0s
[CV] END ...............................alpha=0.4, norm=True; total time=   0.0s
[CV] END ..............................alpha=0.4, norm=False; total time=   0.0s
[CV] END ..............................alpha=0.4, norm=False; total time=   0.0s
[CV] END ..............................alpha=0.4, norm=False; total time=   0.0s
[CV] END ..............................alpha=0.4, norm=False; total time=   0.0s
[CV] END ..............................alpha=0.4, norm=False; total time=   0.0s
[CV] END ...............................alpha=0.5, norm=True; total time=   0.0s
[CV] END ...................

ValueError: 
All the 100 fits failed.
It is very likely that your model is misconfigured.
You can try to debug the error by setting error_score='raise'.

Below are more details about the failures:
--------------------------------------------------------------------------------
100 fits failed with the following error:
Traceback (most recent call last):
  File "/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/model_selection/_validation.py", line 732, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/base.py", line 1151, in wrapper
    return fit_method(estimator, *args, **kwargs)
  File "/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/naive_bayes.py", line 772, in fit
    self._count(X, Y)
  File "/var/tmp/xmacko1/bachelor

In [14]:
scaler_glove = MinMaxScaler()
scaler_glove.fit(X_train_glove)
model, model_params = finetune(
    scaler_glove.transform(X_train_glove), 
    y_train,
    ComplementNB(),
    {
        "norm": [True, False],
        "alpha": [0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9, 1.0],
        
    },
    "f1_micro",
    cv=5,
    verbose=2,
    )
print("Best Hyperparameters:", model_params)
results["naive bayes glove"] = evaluate(scaler_glove.transform(X_test_glove), y_test, model)
print("F1-micro Score on Test Set:", results["naive bayes glove"])

Fitting 5 folds for each of 20 candidates, totalling 100 fits
[CV] END ...............................alpha=0.1, norm=True; total time=   0.0s
[CV] END ...............................alpha=0.1, norm=True; total time=   0.0s
[CV] END ...............................alpha=0.1, norm=True; total time=   0.0s
[CV] END ...............................alpha=0.1, norm=True; total time=   0.0s
[CV] END ...............................alpha=0.1, norm=True; total time=   0.0s
[CV] END ..............................alpha=0.1, norm=False; total time=   0.0s
[CV] END ..............................alpha=0.1, norm=False; total time=   0.0s
[CV] END ..............................alpha=0.1, norm=False; total time=   0.0s
[CV] END ..............................alpha=0.1, norm=False; total time=   0.0s
[CV] END ..............................alpha=0.1, norm=False; total time=   0.0s
[CV] END ...............................alpha=0.2, norm=True; total time=   0.0s
[CV] END ...............................alpha=0

/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/model_selection/_split.py:725: UserWarning: The least populated class in y has only 1 members, which is less than n_splits=5.
  warnings.warn(


[CV] END ...............................alpha=0.2, norm=True; total time=   0.0s
[CV] END ...............................alpha=0.2, norm=True; total time=   0.0s
[CV] END ..............................alpha=0.2, norm=False; total time=   0.0s
[CV] END ..............................alpha=0.2, norm=False; total time=   0.0s
[CV] END ..............................alpha=0.2, norm=False; total time=   0.0s
[CV] END ..............................alpha=0.2, norm=False; total time=   0.0s
[CV] END ..............................alpha=0.2, norm=False; total time=   0.0s
[CV] END ...............................alpha=0.3, norm=True; total time=   0.0s
[CV] END ...............................alpha=0.3, norm=True; total time=   0.0s
[CV] END ...............................alpha=0.3, norm=True; total time=   0.0s
[CV] END ...............................alpha=0.3, norm=True; total time=   0.0s
[CV] END ...............................alpha=0.3, norm=True; total time=   0.0s
[CV] END ...................

## Linear SVM

In [15]:
model, model_params = finetune(
    X_train_word2vec, 
    y_train,
    LinearSVC(loss="squared_hinge", class_weight="balanced", random_state=42),
    {
        "penalty": ["l1", "l2"],
        "C": [0.001, 0.01, 0.1, 1.0, 10.0, 100],
        "intercept_scaling": [0.001, 0.01, 0.1, 1.0, 10.0, 100]
    },
    "f1_micro",
    cv=5,
    verbose=2,
    )
print("Best Hyperparameters:", model_params)
results["linear svm word2vec"] = evaluate(X_test_word2vec, y_test, model)
print("F1-micro Score on Test Set:", results["linear svm word2vec"])

Fitting 5 folds for each of 72 candidates, totalling 360 fits
[CV] END .......C=0.001, intercept_scaling=0.001, penalty=l1; total time=   0.0s
[CV] END .......C=0.001, intercept_scaling=0.001, penalty=l1; total time=   0.0s
[CV] END .......C=0.001, intercept_scaling=0.001, penalty=l1; total time=   0.0s
[CV] END .......C=0.001, intercept_scaling=0.001, penalty=l1; total time=   0.0s
[CV] END .......C=0.001, intercept_scaling=0.001, penalty=l1; total time=   0.0s


/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/model_selection/_split.py:725: UserWarning: The least populated class in y has only 1 members, which is less than n_splits=5.
  warnings.warn(
/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/svm/_classes.py:32: FutureWarning: The default value of `dual` will change from `True` to `'auto'` in 1.5. Set the value of `dual` explicitly to suppress the warning.
  warnings.warn(
/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/svm/_classes.py:32: FutureWarning: The default value of `dual` will change from `True` to `'auto'` in 1.5. Set the value of `dual` explicitly to suppress the warning.
  warnings.warn(
/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/svm/_classes.py:32: FutureWarning: Th

[CV] END .......C=0.001, intercept_scaling=0.001, penalty=l2; total time=   0.6s


/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/svm/_classes.py:32: FutureWarning: The default value of `dual` will change from `True` to `'auto'` in 1.5. Set the value of `dual` explicitly to suppress the warning.
  warnings.warn(


[CV] END .......C=0.001, intercept_scaling=0.001, penalty=l2; total time=   0.6s


...

/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/svm/_base.py:1242: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn(
/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/svm/_classes.py:32: FutureWarning: The default value of `dual` will change from `True` to `'auto'` in 1.5. Set the value of `dual` explicitly to suppress the warning.
  warnings.warn(


[CV] END ...........C=100, intercept_scaling=100, penalty=l2; total time=  29.1s


/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/svm/_base.py:1242: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn(
/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/model_selection/_validation.py:425: FitFailedWarning: 
180 fits failed out of a total of 360.
The score on these train-test partitions for these parameters will be set to nan.
If these failures are not expected, you can try to debug them by setting error_score='raise'.

Below are more details about the failures:
--------------------------------------------------------------------------------
180 fits failed with the following error:
Traceback (most recent call last):
  File "/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/model_selection/_validation.py", line 732, in _fit_and_score

[CV] END ...........C=100, intercept_scaling=100, penalty=l2; total time=  28.3s
Best Hyperparameters: {'C': 0.1, 'intercept_scaling': 100, 'penalty': 'l2'}
F1-micro Score on Test Set: 0.6136865342163356


/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/svm/_base.py:1242: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn(


In [16]:
model, model_params = finetune(
    X_train_glove, 
    y_train,
    LinearSVC(loss="squared_hinge", class_weight="balanced", random_state=42),
    {
        "penalty": ["l1", "l2"],
        "C": [0.001, 0.01, 0.1, 1.0, 10.0, 100],
        "intercept_scaling": [0.001, 0.01, 0.1, 1.0, 10.0, 100]
    },
    "f1_micro",
    cv=5,
    verbose=2,
    )
print("Best Hyperparameters:", model_params)
results["linear svm glove"] = evaluate(X_test_glove, y_test, model)
print("F1-micro Score on Test Set:", results["linear svm glove"])

/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/model_selection/_split.py:725: UserWarning: The least populated class in y has only 1 members, which is less than n_splits=5.
  warnings.warn(
/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/svm/_classes.py:32: FutureWarning: The default value of `dual` will change from `True` to `'auto'` in 1.5. Set the value of `dual` explicitly to suppress the warning.
  warnings.warn(
/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/svm/_classes.py:32: FutureWarning: The default value of `dual` will change from `True` to `'auto'` in 1.5. Set the value of `dual` explicitly to suppress the warning.
  warnings.warn(
/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/svm/_classes.py:32: FutureWarning: Th

Fitting 5 folds for each of 72 candidates, totalling 360 fits
[CV] END .......C=0.001, intercept_scaling=0.001, penalty=l1; total time=   0.0s
[CV] END .......C=0.001, intercept_scaling=0.001, penalty=l1; total time=   0.0s
[CV] END .......C=0.001, intercept_scaling=0.001, penalty=l1; total time=   0.0s
[CV] END .......C=0.001, intercept_scaling=0.001, penalty=l1; total time=   0.0s
[CV] END .......C=0.001, intercept_scaling=0.001, penalty=l1; total time=   0.0s
[CV] END .......C=0.001, intercept_scaling=0.001, penalty=l2; total time=   0.5s


/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/svm/_classes.py:32: FutureWarning: The default value of `dual` will change from `True` to `'auto'` in 1.5. Set the value of `dual` explicitly to suppress the warning.
  warnings.warn(


[CV] END .......C=0.001, intercept_scaling=0.001, penalty=l2; total time=   0.5s


/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/svm/_classes.py:32: FutureWarning: The default value of `dual` will change from `True` to `'auto'` in 1.5. Set the value of `dual` explicitly to suppress the warning.
  warnings.warn(


...

/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/svm/_base.py:1242: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn(
/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/svm/_classes.py:32: FutureWarning: The default value of `dual` will change from `True` to `'auto'` in 1.5. Set the value of `dual` explicitly to suppress the warning.
  warnings.warn(


[CV] END ...........C=100, intercept_scaling=100, penalty=l2; total time=  21.6s


/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/svm/_base.py:1242: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn(
/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/model_selection/_validation.py:425: FitFailedWarning: 
180 fits failed out of a total of 360.
The score on these train-test partitions for these parameters will be set to nan.
If these failures are not expected, you can try to debug them by setting error_score='raise'.

Below are more details about the failures:
--------------------------------------------------------------------------------
180 fits failed with the following error:
Traceback (most recent call last):
  File "/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/model_selection/_validation.py", line 732, in _fit_and_score

[CV] END ...........C=100, intercept_scaling=100, penalty=l2; total time=  21.5s
Best Hyperparameters: {'C': 100, 'intercept_scaling': 10.0, 'penalty': 'l2'}
F1-micro Score on Test Set: 0.5905077262693157


/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/svm/_base.py:1242: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn(


## Random Forest

In [17]:
model, model_params = finetune(
    X_train_word2vec, 
    y_train,
    RandomForestClassifier(class_weight="balanced", random_state=42, n_jobs=-1),
    {
        "min_samples_split": [2, 4, 6, 8, 10, 12, 14, 16, 18, 20],
        "min_samples_leaf": [2, 4, 6, 8, 10, 12, 14, 16, 18, 20],
        "max_samples": [0.6, 0.7, 0.8, 0.9, 1.0]
    },
    "f1_micro",
    cv=5,
    verbose=2,
    )
print("Best Hyperparameters:", model_params)
results["random forest word2vec"] = evaluate(X_test_word2vec, y_test, model)
print("F1-micro Score on Test Set:", results["random forest word2vec"])

/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/model_selection/_split.py:725: UserWarning: The least populated class in y has only 1 members, which is less than n_splits=5.
  warnings.warn(


Fitting 5 folds for each of 500 candidates, totalling 2500 fits
[CV] END max_samples=0.6, min_samples_leaf=2, min_samples_split=2; total time=   0.4s
[CV] END max_samples=0.6, min_samples_leaf=2, min_samples_split=2; total time=   0.4s
[CV] END max_samples=0.6, min_samples_leaf=2, min_samples_split=2; total time=   0.4s
[CV] END max_samples=0.6, min_samples_leaf=2, min_samples_split=2; total time=   0.3s
[CV] END max_samples=0.6, min_samples_leaf=2, min_samples_split=2; total time=   0.5s
[CV] END max_samples=0.6, min_samples_leaf=2, min_samples_split=4; total time=   0.3s
[CV] END max_samples=0.6, min_samples_leaf=2, min_samples_split=4; total time=   0.4s
[CV] END max_samples=0.6, min_samples_leaf=2, min_samples_split=4; total time=   0.3s
[CV] END max_samples=0.6, min_samples_leaf=2, min_samples_split=4; total time=   0.4s
[CV] END max_samples=0.6, min_samples_leaf=2, min_samples_split=4; total time=   0.4s
[CV] END max_samples=0.6, min_samples_leaf=2, min_samples_split=6; total tim

In [18]:
model, model_params = finetune(
    X_train_glove, 
    y_train,
    RandomForestClassifier(class_weight="balanced", random_state=42, n_jobs=-1),
    {
        "min_samples_split": [2, 4, 6, 8, 10, 12, 14, 16, 18, 20],
        "min_samples_leaf": [2, 4, 6, 8, 10, 12, 14, 16, 18, 20],
        "max_samples": [0.6, 0.7, 0.8, 0.9, 1.0]
    },
    "f1_micro",
    cv=5,
    verbose=2,
    )
print("Best Hyperparameters:", model_params)
results["random forest glove"] = evaluate(X_test_glove, y_test, model)
print("F1-micro Score on Test Set:", results["random forest glove"])

Fitting 5 folds for each of 500 candidates, totalling 2500 fits


/var/tmp/xmacko1/bachelor_thesis/.pyenv/versions/3.8.9/envs/ticketing-system/lib/python3.8/site-packages/sklearn/model_selection/_split.py:725: UserWarning: The least populated class in y has only 1 members, which is less than n_splits=5.
  warnings.warn(


[CV] END max_samples=0.6, min_samples_leaf=2, min_samples_split=2; total time=   0.4s
[CV] END max_samples=0.6, min_samples_leaf=2, min_samples_split=2; total time=   0.3s
[CV] END max_samples=0.6, min_samples_leaf=2, min_samples_split=2; total time=   0.4s
[CV] END max_samples=0.6, min_samples_leaf=2, min_samples_split=2; total time=   0.3s
[CV] END max_samples=0.6, min_samples_leaf=2, min_samples_split=2; total time=   0.5s
[CV] END max_samples=0.6, min_samples_leaf=2, min_samples_split=4; total time=   0.3s
[CV] END max_samples=0.6, min_samples_leaf=2, min_samples_split=4; total time=   0.3s
[CV] END max_samples=0.6, min_samples_leaf=2, min_samples_split=4; total time=   0.4s
[CV] END max_samples=0.6, min_samples_leaf=2, min_samples_split=4; total time=   0.3s
[CV] END max_samples=0.6, min_samples_leaf=2, min_samples_split=4; total time=   0.3s
[CV] END max_samples=0.6, min_samples_leaf=2, min_samples_split=6; total time=   0.3s
[CV] END max_samples=0.6, min_samples_leaf=2, min_samp

## Evaluation

In [19]:
pd.DataFrame.from_dict(results, orient="index", columns=["f1 micro"])

f1 micro
dummy most common             0.333333
dummy stratified              0.189845
logistic regression word2vec  0.534216
logistic regression glove     0.565121
naive bayes glove             0.547461
linear svm word2vec           0.613687
linear svm glove              0.590508
random forest word2vec        0.567329
random forest glove           0.588300